# QC Handbook 
## Diamond 2:
### QC Implementations to figure out which subjects should be removed
- Get motion pars for each subject (6 motion 1 FD)
    - calculate min/max/avg
    - Use specific exclusion value for each par
        - Which tasks have unasable motion?
        - What value did it have?
- Run percent coverage script
    - If value is below certain percent threshold, output that ROI
    - If vital areas have dropout, exclude that task
    - What areas are most vital?
- Check to make sure time series was completely collected for task
    - How many timepoints should there be for the task?
        - If it has less than the required timepoints, output the error and exlude that task


In [1]:
import os
import shutil
import sys
import pandas as pd
import glob

### Motion QC Code:

In [2]:
def make_directory(folder):
    import os
    if os.path.exists(folder):
        return True
    else:
        os.mkdir(folder)

In [3]:
def get_file_info(file):
    """Takes in path to confound regressors file and returns subject name and task name"""
    import os
    sub_name = None
    ses_name = 'ses-1'
    task_name = None
    for line in os.path.basename(file).split('_'):
        if 'sub' in line:
            sub_name = line
        elif 'ses' in line:
            ses_name = line
        elif 'task' in line:
            task_name = line
        else:
            continue
    return sub_name, ses_name, task_name

In [4]:
def pull_confounds(tsv, output_path, confounds=['trans_x', 'trans_y', 'trans_z', 'rot_x', 'rot_y', 'rot_z', 'framewise_displacement']):
        """
        this function will pull the regressors specified in 'confounds' from 'tsv' and output a motion.tsv to 'output_path'
        Return pandas dataframe containing confounds
        :param tsv: <string> confounds_timeseries.tsv containing motion parameters
        :param output_path: <string> output path for motion.tsv
        :param confounds: <list> regressors to be used in dataframe
        """
        import pandas as pd
        import os
        
        sub_name, ses_name, task_name = get_file_info(tsv)
        motion_file = os.path.join(output_path, f'{sub_name}_{ses_name}_{task_name}_motion.tsv')
        confounds_file = pd.read_csv(tsv, sep='\t')
        confounds = confounds_file[confounds]
        confounds.to_csv(motion_file, index=None, sep='\t')
        
        return confounds


In [5]:
def generate_metrics(tsv, confounds_df, output_path):
    """
    This function will generate the following metrics for the confounds_df columns:
    count/mean/std/min/25%/50%/75%/max
    
    Uses 'tsv' to extract information about the name of the file
    
    """
    sub_name, ses_name, task_name = get_file_info(tsv)
    confound_metrics = confounds_df.describe()
    confound_metrics_file = os.path.join(output_path, f'{sub_name}_{ses_name}_{task_name}_metrics.tsv')
    confound_metrics.to_csv(confound_metrics_file, sep='\t')
    
    return confound_metrics

In [6]:
def generate_mean_max(fmriprep_dir, task):
    fmriprep_path = os.path.abspath(fmriprep_dir)
    #print(fmriprep_path)
    confounds_files = glob.glob(os.path.join(fmriprep_path, 'sub-*','ses-*','func',f'*{task}*confounds_timeseries.tsv'))
    #print(confounds_files)
    subject_dict = {}
    for file in confounds_files:
        confound_dict = {}
        sub_name, ses_name, task_name = get_file_info(file)
        out_dir = f'{fmriprep_path}/QC_output'
        make_directory(out_dir)
        confounds = pull_confounds(file,out_dir)
        confounds_metrics = generate_metrics(file, confounds, out_dir)
        for col in confounds_metrics:
            confound_dict[f'{col}_mean'] = confounds_metrics[col]['mean']
            confound_dict[f'{col}_max'] = confounds_metrics[col]['max']
        subject_dict[sub_name] = confound_dict
    data = pd.DataFrame(subject_dict).T
    return data

In [7]:
def flag_exclusion_val(df, exclusion_val, metric='mean'):
    """
    This function takes in the output from 'percent_coverage()' and searches for values less than 'exclusion_val' 
    and highlights the values. 
    :param df: <DataFrame> Percent Coverage DataFrame
    :param exlusion_val: <float> Value to search 'df' for
    :param metric: <string> Either 'mean' or 'max'
    """
    def highlight_cols(s):
        color = ''
        if s > exclusion_val:
            color = 'red' 
        return 'background-color: % s' % color
    
    metric_cols = []
    for col in df.columns:
        if metric in col:
            metric_cols.append(col)
    return df[metric_cols].style.applymap(highlight_cols)

In [8]:
class Task_DataFrame:
    def __init__(self, task):
        self.task = task
        self.mean_highlighted = ''
        self.max_highlighted = ''
        self.mean_table = ''
        self.max_table = ''
        self.mean_table_highlighted = ''
        self.max_table_highlighted = ''
        self.mean_excluded = ''
        self.max_excluded = ''

In [9]:
#Section to set tasks and fmriprep_dir
tasks = [Task_DataFrame('reward1'), Task_DataFrame('reward2'), Task_DataFrame('efnback1'), Task_DataFrame('efnback2'), Task_DataFrame('dynface'), Task_DataFrame('rest')]
fmriprep_dir = "./Preprocessed/NON"

In [10]:
for task in tasks:
    task_name = task.task
    task_df = generate_mean_max(fmriprep_dir, task_name)
    task.mean_highlighted = flag_exclusion_val(task_df, 0.7, 'mean') #flag mean values greater than 0.7
    #display(task.mean_highlighted)
    task.max_highlighted = flag_exclusion_val(task_df, 5, 'max') #flag max values greater than 5
    #display(task.max_highlighted)
    task.mean_table = task_df[(task_df['framewise_displacement_max'] > 5) | (task_df['trans_z_max'] > 5) | (task_df['trans_y_max'] > 5) | (task_df['trans_x_max'] > 5)]
    task.max_table = task_df[(task_df['framewise_displacement_mean'] > 0.5) | (task_df['trans_z_mean'] > 0.5) | (task_df['trans_y_mean'] > 0.5) | (task_df['trans_x_mean'] > 5)]
    task.max_table_highlighted = flag_exclusion_val(task_df[(task_df['framewise_displacement_max'] > 5) | (task_df['trans_z_max'] > 5) | (task_df['trans_y_max'] > 5) | (task_df['trans_x_max'] > 5)], 5, 'max')
    task.mean_table_highlighted = flag_exclusion_val(task_df[(task_df['framewise_displacement_mean'] > 0.5) | (task_df['trans_z_mean'] > 0.5) | (task_df['trans_y_mean'] > 0.5) | (task_df['trans_x_mean'] > 0.5)], 0.5, 'mean')
    task.mean_excluded = task.mean_table['framewise_displacement_mean'].count()
    task.max_excluded = task.max_table['framewise_displacement_max'].count()
    print("\n \n \n")

In [11]:
tasks[0].mean_excluded

14

### Example operations to do with DataFrames

In [12]:
#How to get mean_table values
tasks[0].mean_table['rot_x_mean'] # set the column name you would like to select

sub-50108    0.003726
sub-50054    0.050024
sub-50007    0.033033
sub-50010   -0.001603
sub-50078    0.008756
sub-50126   -0.008839
sub-50183   -0.007624
sub-50111    0.026256
sub-50018    0.003998
sub-50122   -0.053747
sub-50581   -0.025598
sub-50187   -0.000084
sub-50097   -0.003762
sub-50004    0.025200
Name: rot_x_mean, dtype: float64

### Percent Coverage Code

In [13]:
atlas = "percent_coverage/bnatlas.nii.gz"
atlas_txt = "percent_coverage/bnatlas.nii.txt"
fmriprep_dir = './Preprocessed/NON'
tasks = ['reward1', 'reward2', 'efnback1', 'efnback2', 'dynface', 'rest']

In [14]:
def percent_coverage(atlas, atlas_txt, fmriprep_dir, task_name):
    """
    This function will return a pandas dataframe which contains ROIs specified by 'atlas'.
    The dataframe will show the percentage of voxels found compared to the maximum possible count found in each ROI.
    This will automatically be done on all subjects found in 'fmriprep_dir' with the specified 'task_name'
    
    :param atlas: <string> path to atlas file
    :param atlas_txt: <string> path to atlas file containing ROI names
    :param fmriprep_dir: <string> path to directory containing fmriprep pre-processed images
    :param task_name: <string> task that you wish to generate percent_coverage output for i.e. ('dynface, reward1, efnback2, ...')
    """
    
    import nibabel as nib
    import numpy as np
    import pandas as pd
    from nilearn import image, masking
    from nilearn.input_data import NiftiMasker, NiftiLabelsMasker
    import os.path
    import glob
    
    atlas_file = glob.glob(atlas)
    print(fmriprep_dir)
    fmri_files_path = os.path.join(fmriprep_dir, 'sub-*', 'ses-1', 'func',f'*{task_name}*preproc_bold.nii*')
    fmri_files = sorted(glob.glob(fmri_files_path))
    fmri_files = atlas_file + fmri_files
    print(fmri_files)
    csv_output = f'{fmriprep_dir}/QC_output/{task_name}_percentcoverage.tsv'
    atlas_img = nib.load(atlas)
    roi_indices, roi_counts = np.unique(atlas_img.get_data(),
    return_counts=True)
    roi_indices = roi_indices[:247]
    roi_counts = roi_counts[:247]
    #ROI names
    f = open(atlas_txt, 'r+')
    rois = [line.strip('\n') for line in f.readlines()]
    #remove the empty string at the end of the list
    rois.pop()
    f.close()

    #Dictionary that will be converted to csv
    '''key = subject_id
        value = dictionary where key is roi_name and value is number of voxels
    '''
    subject_dict = {}
    signal_dict = {}
    #Search through subject in the fmri_files directory
    for subject in fmri_files:
        sub_id = os.path.basename(subject)[:9]
        #print(sub_id)
        roi_dict = {}
        roi_signal_dict = {}
        #roi_dict['subject'] = sub_id
        sub_mean = image.mean_img(subject)

        sub_mean_mask = image.math_img("1. * i.astype(bool)", i=sub_mean)
        masker = NiftiLabelsMasker(atlas_img)
        voxel_ratios = masker.fit_transform([sub_mean_mask])
        #Get total signal strength in each ROI and output to np.Array form
        signal_strength = masker.fit_transform([sub_mean])

        #Get number of voxels present for each roi
        n_voxels = voxel_ratios[0,:] * roi_counts[1:]
        avg_signal_strength = signal_strength[0]/n_voxels
        i=1
        #Create the dictionary with the roi name and value 
        for roi in n_voxels:
            roi_dict[rois[i-1]] = roi
            #print(f'roi {i} has {roi} voxels')
            i+=1
        subject_dict[sub_id] = roi_dict
        #print(f"subject_dict for {sub_id} is {subject_dict[sub_id]}")
        j=1
        for roi in avg_signal_strength:
            roi_signal_dict[rois[j-1]] = roi
            j+=1
        signal_dict[sub_id] = roi_signal_dict
    #Convert the dataframe to a csv 
    #data = pd.DataFrame(subject_dict).T.reset_index().rename(columns={'index':'sub-id'})[rois]
    data = pd.DataFrame(subject_dict).T
    data = data.div(data.iloc[0])
    data.to_csv(csv_output, sep='\t')
    
    return data

In [15]:
def output_low_coverage(pc_df, exclusion_val):
    """
    This function takes in the output from 'percent_coverage()' and searches for values less than 'exclusion_val' 
    and highlights the values. 
    :param pc_df: <DataFrame> Percent Coverage DataFrame
    :param exlusion_val: <float> Value to search 'pc_df' for
    """
    def highlight_cols(s):
        color = ''
        if s < exclusion_val:
            color = 'red' 
        return 'background-color: % s' % color
    return pc_df.style.applymap(highlight_cols)

In [16]:
tasks = ['reward1']

In [17]:
for task in tasks:
    pc_df = percent_coverage(atlas, atlas_txt, fmriprep_dir, task)
    display(output_low_coverage(pc_df, 0.20))

./Preprocessed/NON
['percent_coverage/bnatlas.nii.gz', './Preprocessed/NON/sub-50002/ses-1/func/sub-50002_ses-1_task-reward1_run-1_space-MNI152NLin6Asym_res-2_desc-preproc_bold.nii.gz', './Preprocessed/NON/sub-50004/ses-1/func/sub-50004_ses-1_task-reward1_run-1_space-MNI152NLin6Asym_res-2_desc-preproc_bold.nii.gz', './Preprocessed/NON/sub-50006/ses-1/func/sub-50006_ses-1_task-reward1_run-1_space-MNI152NLin6Asym_res-2_desc-preproc_bold.nii.gz', './Preprocessed/NON/sub-50007/ses-1/func/sub-50007_ses-1_task-reward1_run-1_space-MNI152NLin6Asym_res-2_desc-preproc_bold.nii.gz', './Preprocessed/NON/sub-50008/ses-1/func/sub-50008_ses-1_task-reward1_run-1_space-MNI152NLin6Asym_res-2_desc-preproc_bold.nii.gz', './Preprocessed/NON/sub-50009/ses-1/func/sub-50009_ses-1_task-reward1_run-1_space-MNI152NLin6Asym_res-2_desc-preproc_bold.nii.gz', './Preprocessed/NON/sub-50010/ses-1/func/sub-50010_ses-1_task-reward1_run-1_space-MNI152NLin6Asym_res-2_desc-preproc_bold.nii.gz', './Preprocessed/NON/sub-5001

/tmp/ipykernel_25400/1078106530.py:29: DeprecationWarning: get_data() is deprecated in favor of get_fdata(), which has a more predictable return type. To obtain get_data() behavior going forward, use numpy.asanyarray(img.dataobj).

* deprecated from version: 3.0
* Will raise <class 'nibabel.deprecator.ExpiredDeprecationError'> as of version: 5.0
  roi_indices, roi_counts = np.unique(atlas_img.get_data(),
/tmp/ipykernel_25400/1078106530.py:63: RuntimeWarning: invalid value encountered in true_divide
  avg_signal_strength = signal_strength[0]/n_voxels
/tmp/ipykernel_25400/1078106530.py:63: RuntimeWarning: invalid value encountered in true_divide
  avg_signal_strength = signal_strength[0]/n_voxels
/tmp/ipykernel_25400/1078106530.py:63: RuntimeWarning: invalid value encountered in true_divide
  avg_signal_strength = signal_strength[0]/n_voxels
/tmp/ipykernel_25400/1078106530.py:63: RuntimeWarning: invalid value encountered in true_divide
  avg_signal_strength = signal_strength[0]/n_voxels
